In [1]:
# 在xgboost模型的基础上我要做个伪标签半监督学习，具体思路可以参考这篇博客
# 具体采取的思想是self-training
# http://www.ituring.com.cn/article/497296

In [1]:
import pandas as pd

data_combine = pd.read_excel('D:/大学/大三上/数据挖掘/作业/数据.xlsx')

In [2]:
data_combine_copy = data_combine.copy

In [3]:
data_combine = data_combine_copy()

In [4]:
data_combine = data_combine.drop(['text','word_split'],axis=1)

In [5]:
data_combine = data_combine.drop(['id'],axis=1)

In [19]:
train_data = data_combine[:-8392]

In [20]:
test_data = data_combine[-8392:]

In [21]:
test_data = test_data.drop('author',axis=1)

In [22]:
author_mapping_dict = {'EAP':0, 'HPL':1, 'MWS':2}
train_label = train_data['author'].map(author_mapping_dict)
train_data = train_data.drop('author',axis=1)

In [23]:
from sklearn.model_selection import train_test_split
from sklearn import metrics

In [29]:
train_data_train,train_data_cv,target_train,target_cv = train_test_split(train_data,train_label,test_size=0.2)
import xgboost as xgb
xgb_matrix = xgb.DMatrix(train_data_train,target_train)
param = {}
param['objective'] = 'multi:softprob'
param['eta'] = 0.3
param['max_depth'] = 3
param['silent'] = 1
param['num_class'] = 3
param['eval_metric'] = "mlogloss"
param['min_child_weight'] = 1
param['subsample'] = 0.8
param['colsample_bytree'] = 0.2
param['seed'] = 0
num_rounds =100
model = xgb.cv(params=list(param.items()),dtrain=xgb_matrix,num_boost_round=num_rounds,early_stopping_rounds=50)

In [ ]:
# 有一个bug一直没发现，赋值的时候要用values
b = []
c = []
t = 0.999
th = 0.999
for i in range(1):
    train_data_train,train_data_cv,target_train,target_cv = train_test_split(train_data,train_label,test_size=0.2)
    import xgboost as xgb
    xgb_matrix = xgb.DMatrix(train_data_train,target_train)
    param = {}
    param['objective'] = 'multi:softprob'
    param['eta'] = 0.3
    param['max_depth'] = 3
    param['silent'] = 1
    param['num_class'] = 3
    param['eval_metric'] = "mlogloss"
    param['min_child_weight'] = 1
    param['subsample'] = 0.8
    param['colsample_bytree'] = 0.2
    param['seed'] = 0
    num_rounds =100
    model = xgb.train(params=list(param.items()),dtrain=xgb_matrix,num_boost_round=num_rounds)
for i in range(50):
    t = th
    print(t)
    if t<0.9:
        break
    a = []
    test_lable = model.predict(xgb.DMatrix(test_data))
    c.append(metrics.log_loss(target_cv,model.predict(xgb.DMatrix(train_data_cv))))
    for i in test_lable:
        max_prab = max(i.tolist())
        print(i.tolist())
        max_index = i.tolist().index(max_prab)
        a.append([max_prab,max_index])
    a = pd.DataFrame(a,columns=['max_prab','author'])
    test_data['max_prab'] = a.max_prab.values
    test_data_train = test_data[test_data.max_prab>t]
    test_data_train = test_data_train.drop('max_prab',axis=1)
    print(test_data_train.shape)
    try:
        test_data = test_data[test_data.max_prab<=t]
        th = test_data['max_prab'].quantile(0.99)
        test_data = test_data.drop('max_prab',axis=1)
        a = a[a.max_prab>t]
        a = a.drop('max_prab',axis=1)
        print(test_data.shape)
    except:
        print('matrix wrong')
    try:
        model.update(dtrain=xgb.DMatrix(test_data_train,a),iteration=50)
    except:
        print('xgb_matrix_wrong')
    res = model.predict(xgb.DMatrix(train_data_cv))
    b.append(metrics.log_loss(target_cv,res))

0.999
[0.018810655921697617, 0.009360436350107193, 0.9718288779258728]
[0.9948541522026062, 0.0029699141159653664, 0.002176003297790885]
[0.0036442524287849665, 0.993766188621521, 0.0025895866565406322]
[0.8759394884109497, 0.11865312606096268, 0.005407399497926235]
[0.9463297128677368, 0.030170774087309837, 0.023499587550759315]
[0.9857839941978455, 0.011169511824846268, 0.0030464569572359324]
[0.9018417000770569, 0.09097392112016678, 0.0071843513287603855]
[0.016036540269851685, 0.7084951400756836, 0.27546828985214233]
[0.997484564781189, 0.0011192047968506813, 0.001396233681589365]
[0.9624095559120178, 0.011388345621526241, 0.026202114298939705]
[0.01588420197367668, 0.00756903737783432, 0.9765467643737793]
[0.000281281303614378, 0.9995850920677185, 0.00013367227802518755]
[0.24932396411895752, 0.4963286817073822, 0.2543472945690155]
[0.0029307010117918253, 0.9962055683135986, 0.0008636594284325838]
[0.662394642829895, 0.023192115128040314, 0.31441324949264526]
[0.005338579881936312

In [12]:
sum(c)/len(c)

0.30688651848083703

In [13]:
sum(b)/len(b)

0.30802040780037399

In [14]:
c

[0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30546047837447704,
 0.30546829228171285,
 0.30543498358194604,
 0.30547148893924503,
 0.30541962270273687,
 0.3054025668942032,
 0.30558077558903368,
 0.30654832

In [15]:
b

[0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30542294486245281,
 0.30546047837447704,
 0.30546829228171285,
 0.30543498358194604,
 0.30547148893924503,
 0.30541962270273687,
 0.3054025668942032,
 0.30558077558903368,
 0.3065483244988495,
 0.309308902

In [17]:
data_combine.max()

text_len                  876.000000
symbol_num                 51.000000
symbol_num_,               48.000000
symbol_num_.                7.000000
symbol_num_?                5.000000
symbol_num_:                5.000000
symbol_num_'               14.000000
stopword_num              446.000000
word_mean_length            9.250000
char_num                 3794.000000
unique_word               426.000000
svd_word_1to4gram_0         0.652183
svd_word_1to4gram_1         0.716205
svd_word_1to4gram_2         0.893563
svd_word_1to4gram_3         0.790363
svd_word_1to4gram_4         0.748081
svd_word_1to4gram_5         0.676523
svd_word_1to4gram_6         0.605179
svd_word_1to4gram_7         0.578194
svd_word_1to4gram_8         0.715051
svd_word_1to4gram_9         0.632683
svd_word_1to4gram_10        0.675209
svd_word_1to4gram_11        0.556294
svd_word_1to4gram_12        0.610327
svd_word_1to4gram_13        0.326016
svd_word_1to4gram_14        0.390178
svd_word_1to4gram_15        0.442979
s